In [54]:
import folium
import pandas as pd
from shapely.geometry import Point, MultiPoint
import geopandas as gpd

In [55]:
cluster_df = pd.read_csv("clustering_result.csv")
cluster_df = cluster_df[cluster_df['cluster'] != -1].copy()
print(cluster_df.shape)
cluster_df.head()

(4396, 6)


centroid_lat  centroid_lon  pred  cluster  pred_sum  pred_rank
0     37.561427    126.806755     0        0      14.0       23.0
1     37.562328    126.806729     0        0      14.0       23.0
2     37.563228    126.806702     1        0      14.0       23.0
3     37.564129    126.806676     0        0      14.0       23.0
4     37.561448    126.807887     0        0      14.0       23.0

In [56]:
cluster_df['geometry'] = cluster_df.apply(lambda row: Point(row['centroid_lon'], row['centroid_lat']), axis=1)

# GeoDataFrame 변환
gdf = gpd.GeoDataFrame(cluster_df, geometry='geometry')
# 클러스터별 다각형 만들기
cluster_polygons = gdf.groupby('cluster')['geometry'].apply(lambda points: MultiPoint(list(points)).convex_hull).reset_index()
cluster_polygons = gpd.GeoDataFrame(cluster_polygons, geometry='geometry')

# 각 클러스터의 pred_rank 병합
rank_df = cluster_df[['cluster', 'pred_rank']].drop_duplicates(subset='cluster')
cluster_polygons = cluster_polygons.merge(rank_df, on='cluster')

In [57]:
cluster_polygons = cluster_polygons.merge(risk_ratio_df, on='cluster')

In [58]:
# 지도 중심은 임의 지정
m = folium.Map(location=[37.561427, 126.806755], zoom_start=12)


for _, row in cluster_df.iterrows():
    color = 'red' if row['pred'] == 2 else 'yellow'
    folium.CircleMarker(
        location=[row['centroid_lat'], row['centroid_lon']],
        radius=6,
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.8,
        tooltip=f"Risk: {row['pred']}, Cluster: {row['cluster']}"
    ).add_to(m)

for _, row in cluster_polygons.iterrows():
    folium.GeoJson(
        row['geometry'],
        style_function=lambda x: {
            'fillColor': 'blue',
            'color': 'black',
            'weight': 2,
            'fillOpacity': 0.3
        },
        tooltip=folium.Tooltip(f"Cluster {row['cluster']}<br>pred_rank: {row['pred_rank']}")
    ).add_to(m)
    
# 지도 출력
m

In [59]:
m.save("cluster_map.html")